# BILLE SUR GLISSIÈRE. EXPERIMENT

In [50]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import math

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
from IPython.display import HTML

from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.models import Arrow, OpenHead, NormalHead, VeeHead
output_notebook()

Loading BokehJS ...

### Import data from analysed video and video

In [ ]:
import io
import base64
from IPython.display import HTML

In [3]:
video = io.open('data_bille/exp8-h7-avec-retour.mov', 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="test" controls>
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii')))

### Graphics

Trajectory and free parabola

In [46]:
df = pd.read_csv('data_bille/loop-try1.csv', index_col=0)
df = df.rename({'VideoAnalysis: X (cm)': 'x', 'VideoAnalysis: Y (cm)':'y',
       'VideoAnalysis: X Velocity (cm/s)':'v_x', 'VideoAnalysis: Y Velocity (cm/s)':'v_y'}, axis='columns')

y_min = df['y'].min()
#y_max = df['y'].max()
x_min = df['x'].min()
x_max = df['x'].max()
x_lowest = df.loc[df['y'] == y_min]['x'].iloc[0]

# Set lowest point to (0,0)
df['y'] += -y_min
df['x'] += -x_lowest


In [63]:
"""
TODO:

* CORRECT AXIS
* MEASURE RADIUS AND CORRECT
* ADD VELOCITY VECTOR
* PLOT POINT AT INITIAL HEIGHT AND DETACHMENT POINT

*MATCH VIDEO AS BACKGROUND¿?
"""

g = 9.81
R = 12.5
h = R
omega = 20
to_rad = lambda x: np.pi*x/180.0
omegarad = to_rad(omega)

# Define data to plot
x = -df['x']
y = df['y']

v_a = math.sqrt(2*(g*h - g*R*(1 - np.sin(omegarad))))
t = np.linspace(0, 3, 1000)

x_p = -v_a*np.sin(omegarad)*t + R*np.cos(omegarad)
y_p = -0.5*g*t*t + v_a*np.cos(omegarad)*t + R*(1 + np.sin(omegarad))

# Define plot
p = figure(title="Trajectory", plot_height=300, plot_width=600,
           background_fill_color='#efefef')

# Background image 
glissiere = p.line(x, y, color="#cccccc", line_width=1.5, alpha=0.8)

#Parabola
parab = p.line(x_p, y_p, color='#000000', line_width=1, alpha=0.5)




def update(h, omega):
    omegarad = to_rad(omega)
    
    v_a = math.sqrt(2*(g*h - g*R*(1 - np.sin(omegarad))))
    parab.data_source.data['x'] = -v_a*np.sin(omegarad)*t + R*np.cos(omegarad)
    parab.data_source.data['y'] = -0.5*g*t*t + v_a*np.cos(omegarad)*t + R*(1 + np.sin(omegarad))
    
    push_notebook()

show(p, notebook_handle=True)

interact(update, h=(R, 3*R), omega=(0, 90));

interactive(children=(FloatSlider(value=25.0, description='h', max=37.5, min=12.5), IntSlider(value=45, descri…